# Шаг 1 — парсинг данных (Яндекс Карты)

**Задача:** собрать исходные данные для дальнейшего анализа отзывов:
1) список точек бренда-фокуса («Золотое Яблоко») из Яндекс Карт,
2) отзывы по каждой точке,
3) профили авторов и их отзывы по другим местам/брендам (история посещений).

Парсинг реализован через **Selenium** (браузерный скрейпинг), с рандомными задержками и ротацией User-Agent.


## Что делает ноутбук

###  1) Парсинг списка магазинов (точек бренда)
- Открывает `COMPANY_URL` и скроллит выдачу.
- Для каждой карточки собирает: название, адрес, рейтинг, число оценок, ссылку на отзывы (и/или org_id).
- Сохраняет результат в `stores_zy_step1.csv`.

###  2) Парсинг отзывов по каждой точке
- Берёт `stores_zy_step1.csv` и по очереди открывает страницу отзывов каждой точки.
- Скроллит отзывы, извлекает ключевые поля (дата, рейтинг, текст, автор и т.п.).
- Поддерживает докачку: если файл уже существует, пропускает точки, которые уже собраны.
- Сохраняет результат в `reviews_zy_step2.csv`.

###  3) Парсинг отзывов авторов (история посещений)
- Берёт список авторов (`authors_to_parse_2023_2025.csv`) и проходит по профилям.
- Собирает:
  - профили авторов (агрегаты/метаданные) - `authors_zy_step3_profiles_v2.csv`
  - отзывы авторов по другим местам/брендам (в заданном диапазоне лет) - `authors_reviews_zy_step3_v2.csv`
- Реализована докачка: если часть авторов уже обработана, они пропускаются.
- Пишет технический лог выполнения в `parsing_log_step3.txt`.

---

## Артефакты

- `stores_zy_step1.csv` — список точек бренда-фокуса (магазины/организации) + ссылки на отзывы  
- `reviews_zy_step2.csv` — отзывы по точкам бренда-фокуса  
- `authors_zy_step3_profiles_v2.csv` — профили авторов (агрегированные сведения)  
- `authors_reviews_zy_step3_v2.csv` — отзывы этих авторов по другим местам/брендам  
- `parsing_log_step3.txt` — лог прогресса парсинга авторов

---

## Примечания и ограничения

- Парсинг через Selenium зависит от структуры страниц Яндекс Карт; при изменении верстки могут потребоваться правки CSS-селекторов.
- Возможны капчи/лимиты; используется ротация User-Agent и задержки, но иногда требуется ручное вмешательство.
- Скорость работы зависит от числа точек/авторов и стабильности соединения.


# 1) Парсим список магазинов

In [41]:
import time
import random
import re
import pandas as pd
from urllib.parse import urlparse, urlunparse, urljoin
from datetime import datetime

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    NoSuchElementException,
    TimeoutException,
    StaleElementReferenceException,
)

COMPANY_URL = "https://yandex.com/maps/?display-text=%D0%97%D0%BE%D0%BB%D0%BE%D1%82%D0%BE%D0%B5%20%D0%AF%D0%B1%D0%BB%D0%BE%D0%BA%D0%BE&ll=83.113357%2C16.390862&mode=search&sctx=ZAAAAAgBEAAaKAoSCcL4adybU1pAEdMzvcRYEkdAEhIJAAAAAIAuZUAR4BRWKigPYEAiBgABAgMEBSgKOABAkE5IAWoCcnWdAc3MzD2gAQCoAQC9AY99zHTCAY4BxJXEm5YD4M%2BEvvMGid%2Bo99AGgLi8gmXzu7TZgwWu45WU5AHVqvGXlAbv6KzLH%2BGw0%2FPwBeyLxt4DzJHD%2BgOZr7%2BIeej6r%2Fv7Av6rqcpWpLCjxaUByKO88ATb%2B9DYiAWY1eLFggb8vfzcA%2FfzzqrsBviBspmKB7fluIKOBOSbyYfoBb2N9PjjBIi9yZfBBYICGigoY2hhaW5faWQ6KDM0MTE0MTgwMDI0KSkpigIAkgIAmgIMZGVza3RvcC1tYXBzqgILMzQxMTQxODAwMjSwAgE%3D&sll=83.113357%2C16.390862&sspn=266.132813%2C141.505033&text=%7B%22text%22%3A%22%D0%97%D0%BE%D0%BB%D0%BE%D1%82%D0%BE%D0%B5%20%D0%AF%D0%B1%D0%BB%D0%BE%D0%BA%D0%BE%22%2C%22what%22%3A%5B%7B%22attr_name%22%3A%22chain_id%22%2C%22attr_values%22%3A%5B%2234114180024%22%5D%7D%5D%7D&z=2"
OUTPUT_CSV = "stores_zy_step1.csv"

USER_AGENTS = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4389.90 Safari/537.36",
]


def configure_browser():
    opts = webdriver.ChromeOptions()
    opts.add_argument("--disable-blink-features=AutomationControlled")
    opts.add_argument("--start-maximized")
    opts.add_argument(f"user-agent={random.choice(USER_AGENTS)}")
    driver = webdriver.Chrome(options=opts)
    driver.set_page_load_timeout(60)
    driver.set_script_timeout(60)
    return driver


def safe_find(el, sel, attr=None, default=None):
    try:
        found = el.find_element(By.CSS_SELECTOR, sel)
        return found.get_attribute(attr) if attr else found
    except NoSuchElementException:
        return default


def normalize_url(url: str) -> str:
    p = urlparse(url)
    return urlunparse(p._replace(query="", fragment=""))


def locate_scroller(driver):
    # контейнер списка карточек
    try:
        ul = driver.find_element(By.CSS_SELECTOR, "ul.search-list-view__list")
    except NoSuchElementException:
        return driver.find_element(By.TAG_NAME, "body")

    el = ul
    while el:
        if driver.execute_script(
            "return arguments[0].scrollHeight > arguments[0].clientHeight;", el
        ):
            return el
        el = driver.execute_script("return arguments[0].parentElement;", el)

    return driver.find_element(By.TAG_NAME, "body")


def collect_stores(driver):
    """Собираем список магазинов ЗЯ: название, адрес, рейтинг, количество оценок, ссылку на отзывы."""
    print("Открываю страницу сети ЗЯ...")
    try:
        driver.get(COMPANY_URL)
    except TimeoutException:
        print(" Страница сети грузилась дольше таймаута, но продолжаем")

    # ждём появления хотя бы одной карточки
    WebDriverWait(driver, 60).until(
        EC.presence_of_element_located(
            (By.CSS_SELECTOR, "div.search-business-snippet-view__content")
        )
    )
    print("Первая карточка найдена, начинаю скроллить")

    scroller = locate_scroller(driver)

    seen_urls = set()
    seen_stores = set()
    stores = []

    no_new_rounds = 0          # сколько итераций подряд не появлялось новых магазинов
    add_block_rounds = 0       # сколько раз подряд мы видим блок add-business-view
    MAX_ROUNDS = 60            # максимальное количество итераций защиты от бесконечного цикла

    for round_idx in range(MAX_ROUNDS):
        try:
            cards = scroller.find_elements(
                By.CSS_SELECTOR,
                "div.search-business-snippet-view__content"
            )
        except StaleElementReferenceException:
            scroller = locate_scroller(driver)
            cards = scroller.find_elements(
                By.CSS_SELECTOR,
                "div.search-business-snippet-view__content"
            )

        before_urls = len(seen_urls)

        print(f"[{round_idx+1}/{MAX_ROUNDS}] вижу карточек: {len(cards)}, уникальных URL: {before_urls}")

        for card in cards:
            #  название 
            title = safe_find(
                card,
                "div.search-business-snippet-view__title",
                "textContent",
                ""
            ).strip()

            title_lower = title.lower()

            # фильтруем только наши магазины (без «Похожих организаций»)
            if "золотое яблоко" not in title_lower:
                continue

            #  адрес 
            addr = (
                safe_find(card, "a.search-business-snippet-view__address", "textContent", "")
                or safe_find(card, "div.search-business-snippet-view__address", "textContent", "")
            ).strip()

            #  защита от дублей по названию+адресу
            store_key = (title_lower, addr)
            if store_key in seen_stores:
                continue
            seen_stores.add(store_key)


            #  рейтинг 
            rating_text = safe_find(
                card,
                "span.business-rating-badge-view__rating-text",
                "textContent",
                ""
            )
            if rating_text:
                rating_text = rating_text.strip().replace(",", ".")
                try:
                    avg_rating = float(rating_text)
                except ValueError:
                    avg_rating = None
            else:
                avg_rating = None

            #  количество оценок 
            count_text = safe_find(
                card,
                "div.business-rating-with-text-view__count span",
                "textContent",
                ""
            )
            if count_text:
                m = re.search(r"[\d\s]+", count_text)
                reviews_count = int(m.group(0).replace(" ", "")) if m else None
            else:
                reviews_count = None

            #  ссылка на отзывы 
            rating_link = safe_find(
                card,
                "a.search-business-snippet-view__rating",
                "href",
                None
            )

            if rating_link:
                reviews_url = normalize_url(urljoin("https://yandex.ru", rating_link))
            else:
                reviews_url = None

            # дубликаты режем только если есть reviews_url
            if reviews_url and reviews_url in seen_urls:
                continue
            if reviews_url:
                seen_urls.add(reviews_url)
            
            print("  НАШЛА:", title, "|", addr, "| url:", reviews_url)


            stores.append(
                {
                    "store_name":    title,
                    "address_raw":   addr,
                    "avg_rating":    avg_rating,
                    "reviews_count": reviews_count,
                    "reviews_url":   reviews_url,
                    "parsed_at":     datetime.now(),
                }
            )


        #  проверяем, появились ли новые магазины 
        after_urls = len(seen_urls)
        if after_urls == before_urls:
            no_new_rounds += 1
        else:
            no_new_rounds = 0

        #  ищем блок "Добавьте организацию" 
        add_block = driver.find_elements(By.CSS_SELECTOR, "div.add-business-view")
        if add_block:
            add_block_rounds += 1
        else:
            add_block_rounds = 0

        # условие остановки:
        #   - несколько раз подряд не появлялось новых магазинов
        #   - и уже пару раз видели add-business-view (мы точно около футера)
        if no_new_rounds >= 5 and add_block_rounds >= 2:
            print("Похоже, достигли конца списка (нет новых URL, add-business-view уже есть). Останавливаюсь.")
            break

        #  скроллим дальше 
        if cards:
            try:
                last_card = cards[-1]
                # сначала доскроллить до последней карточки
                driver.execute_script(
                    "arguments[0].scrollIntoView({block: 'end'});",
                    last_card
                )
                # затем ещё чуть-чуть вниз, чтобы спровоцировать подгрузку
                driver.execute_script(
                    "arguments[0].scrollTop += arguments[0].clientHeight * 0.3;",
                    scroller
                )
            except StaleElementReferenceException:
                pass

        time.sleep(random.uniform(2.0, 3.0))

    print(f"Найдено магазинов ЗЯ: {len(stores)}")
    return stores



def main():
    driver = configure_browser()
    try:
        stores = collect_stores(driver)
    finally:
        driver.quit()

    df = pd.DataFrame(stores)
    df.to_csv(OUTPUT_CSV, index=False, encoding="utf-8-sig")
    print(f"Сохранено в {OUTPUT_CSV}")
    for row in stores[:5]:
        print(row)


if __name__ == "__main__":
    main()


Открываю страницу сети ЗЯ...
Первая карточка найдена, начинаю скроллить
[1/60] вижу карточек: 5, уникальных URL: 0
  НАШЛА: Золотое яблоко | Москва, Трубная площадь, 2 | url: https://yandex.com/maps/org/gold_apple/109042535108/reviews/
  НАШЛА: Золотое Яблоко | Москва, Павелецкая площадь, 3 | url: https://yandex.com/maps/org/gold_apple/237158606816/reviews/
  НАШЛА: Золотое Яблоко | Санкт-Петербург, Невский просп., 114-116, этаж 1 | url: https://yandex.com/maps/org/gold_apple/27117165568/reviews/
  НАШЛА: Золотое Яблоко | Кировоградская ул., 13А, Москва, этаж 1 | url: https://yandex.com/maps/org/zolotoye_yabloko/227883495305/reviews/
  НАШЛА: Золотое яблоко | Санкт-Петербург, Лиговский просп., 30, этаж 1 | url: https://yandex.com/maps/org/gold_apple/174132051419/reviews/
[2/60] вижу карточек: 7, уникальных URL: 5
  НАШЛА: Золотое яблоко | Краснодар, ул. Володи Головатого, 313, этаж 1 | url: https://yandex.com/maps/org/gold_apple/172791504371/reviews/
  НАШЛА: Золотое яблоко | Москва, п

# 2) Парсим отзывы по магазину

In [48]:
import time
import random
import re
import os
import pandas as pd
from datetime import datetime, timedelta

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    NoSuchElementException, TimeoutException, StaleElementReferenceException
)

STORES_CSV = "stores_zy_step1.csv"
REVIEWS_CSV = "reviews_zy_step2.csv"

#  на время отладки 
MAX_REVIEWS_PER_STORE = None     
DEBUG_PRINT_FIRST_N = 5        # сколько первых отзывов печатать

USER_AGENTS = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4389.90 Safari/537.36",
]

#  утилиты 

def configure_browser():
    opts = webdriver.ChromeOptions()
    opts.add_argument("--disable-blink-features=AutomationControlled")
    opts.add_argument("--start-maximized")
    opts.add_argument(f"user-agent={random.choice(USER_AGENTS)}")
    driver = webdriver.Chrome(options=opts)
    driver.set_page_load_timeout(60)
    driver.set_script_timeout(60)
    return driver

def safe_find(el, sel, attr=None, default=None):
    try:
        found = el.find_element(By.CSS_SELECTOR, sel)
        return found.get_attribute(attr) if attr else found
    except (NoSuchElementException, StaleElementReferenceException):
        return default

def convert_date(text):
    if not text:
        return None

    text = text.lower().strip()
    today = datetime.today().replace(hour=0, minute=0, second=0, microsecond=0)

    months = {
        "января": 1, "февраля": 2, "марта": 3,
        "апреля": 4, "мая": 5, "июня": 6,
        "июля": 7, "августа": 8, "сентября": 9,
        "октября": 10, "ноября": 11, "декабря": 12
    }

    # сегодня / вчера
    if "сегодня" in text:
        return today
    if "вчера" in text:
        return today - timedelta(days=1)

    # N дней назад
    m = re.search(r"(\d+)\s+дн(?:я|ей)?\s+назад", text)
    if m:
        return today - timedelta(days=int(m.group(1)))

    # N недель назад
    m = re.search(r"(\d+)\s+недел(?:ю|и|ь)?\s+назад", text)
    if m:
        return today - timedelta(weeks=int(m.group(1)))

    # N часов назад — для нас всё равно «сегодня»
    m = re.search(r"(\d+)\s+час(?:а|ов)?\s+назад", text)
    if m:
        return today

    # формат "7 октября" или "7 октября 2023"
    m = re.search(r"(\d+)\s+([а-я]+)", text)
    if m:
        day = int(m.group(1))
        month_name = m.group(2)
        month = months.get(month_name)
        if month:
            year_match = re.search(r"\b(\d{4})\b", text)
            year = int(year_match.group(1)) if year_match else today.year
            try:
                return datetime(year, month, day)
            except ValueError:
                return None

    return None


def extract_yandex_org_id(reviews_url: str):
    m = re.search(r"/org/[^/]+/(\d+)", reviews_url)
    return m.group(1) if m else None

#  парсинг одного отзыва 

def parse_review(driver, review_el, org_id, store_row, idx_in_store):
    """Возвращает dict для таблицы REVIEWS, включая ответ организации."""
    #  автор 
    author_link_el = safe_find(review_el, "a.business-review-view__link")
    author_profile_url = author_link_el.get_attribute("href") if author_link_el else None

    author_name = None
    if author_link_el:
        author_name = safe_find(author_link_el, "span", "textContent", "")
        author_name = author_name.strip() if author_name else None

    author_id = None
    if author_profile_url:
        m = re.search(r"/user/([^/?#]+)", author_profile_url)
        if m:
            author_id = m.group(1)

    author_caption = safe_find(
        review_el,
        "div.business-review-view__author-caption",
        "textContent",
        ""
    )
    author_caption = author_caption.strip() if author_caption else None

    #  рейтинг 
    rating = None
    aria = safe_find(
        review_el,
        "div.business-rating-badge-view__stars",
        "aria-label",
        ""
    )
    if aria:
        m = re.search(r"Оценка\s+(\d)", aria)
        if m:
            rating = int(m.group(1))

    #  дата 
    date_text = safe_find(
        review_el,
        "span.business-review-view__date",
        "textContent",
        ""
    )
    review_dt = convert_date(date_text)

    #  раскрываем полный текст отзыва (кнопка «Ещё») 
    more_btn = safe_find(review_el, "span.business-review-view__expand")
    if more_btn and more_btn.is_displayed():
        try:
            # доскроллим, чтобы кнопка точно была в зоне клика
            driver.execute_script(
                "arguments[0].scrollIntoView({block:'center'});",
                more_btn
            )
            # иногда обычный click не срабатывает — жмём через JS
            driver.execute_script("arguments[0].click();", more_btn)
            time.sleep(0.3)
        except Exception:
            pass

    #  текст отзыва 
    body_el = safe_find(review_el, "div.business-review-view__body")
    if body_el:
        text_raw = body_el.get_attribute("textContent") or ""
        text_raw = text_raw.strip()
    else:
        text_raw = None

    #  фотки 
    photos = review_el.find_elements(
        By.CSS_SELECTOR,
        "div.business-review-view__body img"
    )
    photos_count = len(photos)

    #  лайки / дизлайки 
    likes_count = 0
    dislikes_count = 0
    for cont in review_el.find_elements(By.CSS_SELECTOR, "div.business-reactions-view__container"):
        label = cont.get_attribute("aria-label") or ""
        counter_text = safe_find(
            cont,
            "div.business-reactions-view__counter",
            "textContent",
            "0"
        )
        try:
            cnt = int(counter_text)
        except ValueError:
            cnt = 0
        if "Лайк" in label:
            likes_count = cnt
        elif "Дизлайк" in label:
            dislikes_count = cnt

    #  ответ организации 
    org_reply_flag = False
    org_reply_text = None
    org_reply_date = None

    # раскрываем блок «Посмотреть ответ организации»
    comment_expand = safe_find(review_el, "div.business-review-view__comment-expand")
    if comment_expand and comment_expand.is_displayed():
        try:
            driver.execute_script(
                "arguments[0].scrollIntoView({block:'center'});",
                comment_expand
            )
            driver.execute_script("arguments[0].click();", comment_expand)
            time.sleep(0.3)
        except Exception:
            pass

    comment_block = safe_find(review_el, "div.business-review-comment__comment")
    if comment_block:
        org_reply_flag = True
        # дата ответа
        reply_date_text = safe_find(
            comment_block,
            "span.business-review-comment-content__date",
            "textContent",
            ""
        )
        org_reply_date = convert_date(reply_date_text) if reply_date_text else None

        # текст ответа
        reply_text_el = safe_find(
            comment_block,
            "div.business-review-comment-content__bubble"
        )
        if reply_text_el:
            reply_text = reply_text_el.get_attribute("textContent") or ""
            org_reply_text = reply_text.strip() if reply_text else None

    review_id = f"{org_id}_{idx_in_store}"

    row = {
        "review_id": review_id,
        "org_id": org_id,
        "store_name": store_row["store_name"],
        "store_address": store_row["address_raw"],
        "author_id": author_id,
        "author_name": author_name,
        "author_profile_url": author_profile_url,
        "author_caption": author_caption,
        "review_datetime": review_dt,
        "rating": rating,
        "text_raw": text_raw,
        "likes_count": likes_count,
        "dislikes_count": dislikes_count,
        "photos_count": photos_count,
        "org_reply_flag": org_reply_flag,
        "org_reply_date": org_reply_date,
        "org_reply_text": org_reply_text,
        "parsed_at": datetime.now(),
    }

    if idx_in_store <= DEBUG_PRINT_FIRST_N:
        print("  ► пример отзыва:", row["author_name"], "|", date_text)
        print("    текст:", (text_raw or "")[:120], "...\n")

    return row


#  скроллинг и сбор всех отзывов магазина 

def collect_reviews_for_store(driver, store_row, max_reviews_per_store=None):
    reviews_url = store_row["reviews_url"]
    org_id = extract_yandex_org_id(reviews_url) or reviews_url

    print(f"\nОткрываю отзывы для: {store_row['store_name']} — {store_row['address_raw']}")
    print(reviews_url)

    try:
        driver.get(reviews_url)
    except TimeoutException:
        print("⚠ Страница отзывов грузилась дольше таймаута при загрузке, но пробуем дальше")

    # ждём контейнер с отзывами
    container = WebDriverWait(driver, 60).until(
        EC.presence_of_element_located(
            (By.CSS_SELECTOR, "div.business-reviews-card-view__reviews-container")
        )
    )

    all_reviews_els = []
    no_new_rounds = 0
    MAX_ROUNDS = 200

    for round_idx in range(MAX_ROUNDS):
        try:
            reviews_now = container.find_elements(
                By.CSS_SELECTOR,
                "div.business-reviews-card-view__review"
            )
        except StaleElementReferenceException:
            container = driver.find_element(
                By.CSS_SELECTOR,
                "div.business-reviews-card-view__reviews-container"
            )
            reviews_now = container.find_elements(
                By.CSS_SELECTOR,
                "div.business-reviews-card-view__review"
            )

        prev_len = len(all_reviews_els)
        all_reviews_els = reviews_now

        print(f"[{round_idx+1}/{MAX_ROUNDS}] отзывов видно: {len(all_reviews_els)}")

        # лимит на количество отзывов
        if max_reviews_per_store and len(all_reviews_els) >= max_reviews_per_store:
            print(f"Достигли лимита {max_reviews_per_store} отзывов для магазина")
            break

        # проверка стагнации
        if len(all_reviews_els) == prev_len:
            no_new_rounds += 1
        else:
            no_new_rounds = 0

        if no_new_rounds >= 5:
            print("Похоже, отзывы закончились")
            break

        # скроллим к последнему отзыву
        if all_reviews_els:
            last = all_reviews_els[-1]
            try:
                driver.execute_script(
                    "arguments[0].scrollIntoView({block:'end'});",
                    last
                )
            except StaleElementReferenceException:
                pass

        time.sleep(random.uniform(1.0, 2.0))

    # режем по лимиту на всякий случай
    if max_reviews_per_store:
        all_reviews_els = all_reviews_els[:max_reviews_per_store]

    print(f"Всего собрано отзывов для магазина: {len(all_reviews_els)}")

    parsed = []
    for i, rev_el in enumerate(all_reviews_els, start=1):
        parsed.append(parse_review(driver, rev_el, org_id, store_row, i))

    return parsed

#  main 

def main():
    stores_df = pd.read_csv(STORES_CSV)

    # если файл с отзывами уже существует — подхватим его и будем дописывать
    all_reviews = []
    done_org_ids = set()
    if os.path.exists(REVIEWS_CSV):
        existing = pd.read_csv(REVIEWS_CSV)
        all_reviews = existing.to_dict("records")
        if "org_id" in existing.columns:
            done_org_ids = set(existing["org_id"].dropna().unique())
        print(f"Уже есть {len(existing)} отзывов в {REVIEWS_CSV}, магазинов собрано: {len(done_org_ids)}")

    driver = configure_browser()
    try:
        for idx, store_row in stores_df.iterrows():
            store_dict = store_row.to_dict()
            org_id = extract_yandex_org_id(store_dict["reviews_url"]) or store_dict["reviews_url"]

            print(f"\n=== Магазин {idx+1}/{len(stores_df)} ===")
            print(f"{store_dict['store_name']} — {store_dict['address_raw']} (org_id={org_id})")

            # если этот магазин уже есть в файле — можно пропустить
            if org_id in done_org_ids:
                print("  Этот магазин уже собирали, пропускаю")
                continue

            # основной сбор отзывов
            store_reviews = collect_reviews_for_store(
                driver,
                store_dict,
                max_reviews_per_store=MAX_REVIEWS_PER_STORE
            )

            print(f"  Для этого магазина собрано {len(store_reviews)} отзывов")

            all_reviews.extend(store_reviews)
            done_org_ids.add(org_id)

            # промежуточное сохранение
            df = pd.DataFrame(all_reviews)
            df.to_csv(REVIEWS_CSV, index=False, encoding="utf-8-sig")
            print(f"  Промежуточно сохранено {len(df)} отзывов в {REVIEWS_CSV}")

            # пауза между магазинами, чтобы не дразнить Яндекс
            time.sleep(random.uniform(5, 10))

    finally:
        driver.quit()
        print("Браузер закрыт")

    print("\nГотово. Итоговое количество отзывов:", len(all_reviews))


if __name__ == "__main__":
    main()


Уже есть 30 отзывов в reviews_zy_step2.csv, магазинов собрано: 1

=== Магазин 1/34 ===
Золотое яблоко — Москва, Трубная площадь, 2 (org_id=109042535108)

Открываю отзывы для: Золотое яблоко — Москва, Трубная площадь, 2
https://yandex.com/maps/org/gold_apple/109042535108/reviews/
[1/200] отзывов видно: 50
[2/200] отзывов видно: 100
[3/200] отзывов видно: 150
[4/200] отзывов видно: 200
[5/200] отзывов видно: 250
[6/200] отзывов видно: 300
[7/200] отзывов видно: 350
[8/200] отзывов видно: 350
[9/200] отзывов видно: 350
[10/200] отзывов видно: 350
[11/200] отзывов видно: 350
[12/200] отзывов видно: 350
Похоже, отзывы закончились
Всего собрано отзывов для магазина: 350
  ► пример отзыва: Светлана Кушнаренко | 7 октября
    текст: Отличный магазин, один из любимых! Часто заезжаю сюда лично, а также регулярно заказываю косметику и средства гигиены он ...

  ► пример отзыва: Олеся | 30 августа
    текст: Большой магазин с огромным ассортиментом. В пешей доступности от метро.
На полках с парфюм

#  3) Парсим отзывы по автору 

In [108]:
import os
import time
import random
import re
from datetime import datetime
from urllib.parse import urljoin, urlparse

import pandas as pd

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    NoSuchElementException,
    TimeoutException,
    StaleElementReferenceException,
)



#  настройки 

BASE_DIR = r"/Users/anna_maltseva/Desktop/паарсер для диссера"

AUTHORS_TO_PARSE_CSV  = os.path.join(BASE_DIR, "authors_to_parse_2023_2025.csv")
AUTHORS_PROFILES_CSV  = os.path.join(BASE_DIR, "authors_zy_step3_profiles_v2.csv")
AUTHORS_REVIEWS_CSV   = os.path.join(BASE_DIR, "authors_reviews_zy_step3_v2.csv")
LOG_PATH = os.path.join(BASE_DIR, "parsing_log_step3.txt")
TARGET_YEAR_MIN = 2023
TARGET_YEAR_MAX = 2025

MAX_ROUNDS_SCROLL = 300  # защита от бесконечного скролла

USER_AGENTS = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4389.90 Safari/537.36",
]

#  утилиты  

def configure_browser():
    opts = webdriver.ChromeOptions()
    opts.add_argument("--disable-blink-features=AutomationControlled")
    opts.add_argument("--start-maximized")
    opts.add_argument(f"user-agent={random.choice(USER_AGENTS)}")
    driver = webdriver.Chrome(options=opts)
    driver.set_page_load_timeout(60)
    driver.set_script_timeout(60)
    return driver


def safe_find(el, sel, attr=None, default=None):
    try:
        found = el.find_element(By.CSS_SELECTOR, sel)
        return found.get_attribute(attr) if attr else found
    except NoSuchElementException:
        return default


#  разбор дат 

MONTHS = {
    # родительный
    "января": 1, "февраля": 2, "марта": 3, "апреля": 4, "мая": 5, "июня": 6,
    "июля": 7, "августа": 8, "сентября": 9, "октября": 10, "ноября": 11, "декабря": 12,
    # именительный
    "январь": 1, "февраль": 2, "март": 3, "апрель": 4, "май": 5, "июнь": 6,
    "июль": 7, "август": 8, "сентябрь": 9, "октябрь": 10, "ноябрь": 11, "декабрь": 12,
}

def parse_profile_review_date(text: str) -> datetime | None:
    """
    Дата на профиле: 'Ноябрь 2025', 'Июнь 2019' и т.п.
    Возвращаем первое число месяца.
    """
    if not text:
        return None
    t = text.strip().lower()
    m = re.search(r"([а-яё]+)\s+(\d{4})", t)
    if not m:
        return None
    month_name = m.group(1)
    year = int(m.group(2))
    month = MONTHS.get(month_name)
    if not month:
        return None
    return datetime(year, month, 1)


#  медиа (фото / видео) 



def count_media(review_el):
    """
    Считает в отзыве:
      - общее количество медиа
      - отдельно фото
      - отдельно видео

    Логика заточена под структуру:
    - общий контейнер: div.business-review-media__grouped-content
    - фото: <img class="business-review-media__item-img">
    - видео: div.video-player-view (большое) и div.video-thumbnail (элементы карусели)
    """

    media_group = safe_find(review_el, "div.business-review-media__grouped-content")
    if not media_group:
        return 0, 0, 0  # total, photos, videos

    #  фото 
    photo_srcs = set()
    photo_imgs = media_group.find_elements(
        By.CSS_SELECTOR,
        "img.business-review-media__item-img"
    )
    for img in photo_imgs:
        src = img.get_attribute("src")
        if src:
            photo_srcs.add(src)

    #  видео 
    video_ids = set()

    # большое видео + превьюшки в карусели
    video_blocks = media_group.find_elements(
        By.CSS_SELECTOR,
        "div.video-player-view, div.video-thumbnail"
    )

    for block in video_blocks:
        # пробуем вытащить какой-нибудь устойчивый идентификатор
        vid = block.get_attribute("data-video-src")
        if not vid:
            # для thumbnail берём src вложенной картинки
            inner_img = safe_find(block, "img", "src", None)
            vid = inner_img

        # если вообще ничего не нашли — всё равно считаем как один уникальный блок
        if not vid:
            vid = f"block-{id(block)}"

        video_ids.add(vid)

    photos_count = len(photo_srcs)
    videos_count = len(video_ids)
    total = photos_count + videos_count

    return total, photos_count, videos_count



#  разбор одного отзыва с профиля 

def extract_yandex_org_id(url: str) -> str | None:
    """
    /maps/org/gekovi/231120977632/ -> 231120977632
    """
    path = urlparse(url).path
    m = re.search(r"/org/[^/]+/(\d+)", path)
    return m.group(1) if m else None


def parse_profile_review(review_el, author_row, idx_in_author):
    author_id = author_row["author_id"]
    author_name = author_row.get("author_name")
    author_profile_url = author_row.get("author_profile_url")

    #  место (организация) 
    org_link_el = safe_find(review_el, "a.ugc-public-content-view__org")
    place_url = None
    place_org_id = None
    place_name = None
    place_city = None
    place_category = None

    if org_link_el:
        href = org_link_el.get_attribute("href") or ""
        place_url = urljoin("https://yandex.com", href)
        place_org_id = extract_yandex_org_id(place_url)

        place_name = safe_find(
            org_link_el,
            "div.ugc-public-content-view__org-name",
            "textContent",
            ""
        )
        place_name = place_name.strip() if place_name else None

        caption = safe_find(
            org_link_el,
            "div.ugc-public-content-view__public-info-caption",
            "textContent",
            ""
        )
        if caption:
            parts = [p.strip() for p in caption.split("•")]
            if len(parts) >= 1:
                place_city = parts[0]
            if len(parts) >= 2:
                place_category = parts[1]

    #  рейтинг 
    rating = None
    aria = safe_find(
        review_el,
        "div.business-rating-badge-view__stars",
        "aria-label",
        ""
    )
    if aria:
        m = re.search(r"Оценка\s+(\d)\s+Из\s+5", aria)
        if m:
            rating = int(m.group(1))

    #  дата 
    date_text = safe_find(
        review_el,
        "span.ugc-public-content-view__date",
        "textContent",
        ""
    )
    review_dt = parse_profile_review_date(date_text)

    #  раскрываем текст (Показать полностью) 
    more_btn = safe_find(review_el, "span.spoiler-view__button")
    if more_btn:
        try:
            review_el.location_once_scrolled_into_view
            more_btn.click()
            time.sleep(0.2)
        except Exception:
            pass

    text_raw = safe_find(
        review_el,
        "span.spoiler-view__text-container",
        "textContent",
        ""
    )
    text_raw = text_raw.strip() if text_raw else None

    #  медиа 
    media_total = 0
    preview_blocks = []
    carousel_items = []

    # пробуем найти "групповой" контейнер
    media_block = safe_find(review_el, "div.business-review-media__grouped-content")
    # если его нет – считаем по всему отзыву
    container = media_block if media_block else review_el

    #  превью (большая фотка/видео сверху) 
    try:
        preview_blocks = container.find_elements(
            By.CSS_SELECTOR,
            "div.business-review-media._preview-size_expanded"
        )
    except StaleElementReferenceException:
        preview_blocks = []

    preview_count = 1 if preview_blocks else 0

    #  карусель (набор медиа-айтемов) 
    try:
        carousel_items = container.find_elements(
            By.CSS_SELECTOR,
            "div.carousel.business-review-media div.carousel__item._align_center"
        )
    except StaleElementReferenceException:
        carousel_items = []

    carousel_count = len(carousel_items)

    if preview_count or carousel_count:
        media_total = preview_count + carousel_count

    # отладочный вывод для первых 5 карточек
    if idx_in_author <= 5:
        print(
            f"  ▶ медиа: total={media_total}, "
            f"preview={len(preview_blocks)}, "
            f"carousel_items={len(carousel_items)}"
        )


    #  лайки / дизлайки 
    likes_count = 0
    dislikes_count = 0
    for cont in review_el.find_elements(By.CSS_SELECTOR, "div.business-reactions-view__container"):
        label = cont.get_attribute("aria-label") or ""
        counter_text = safe_find(cont, "div.business-reactions-view__counter", "textContent", "0")
        try:
            cnt = int(counter_text)
        except ValueError:
            cnt = 0
        if "Лайк" in label:
            likes_count = cnt
        elif "Дизлайк" in label:
            dislikes_count = cnt

    row = {
        "author_id": author_id,
        "author_name": author_name,
        "author_profile_url": author_profile_url,
        "review_idx_in_author": idx_in_author,
        "place_org_id": place_org_id,
        "place_name": place_name,
        "place_city": place_city,
        "place_category": place_category,
        "place_url": place_url,
        "rating": rating,
        "review_datetime": review_dt,
        "review_year": review_dt.year if review_dt else None,
        "text_raw": text_raw,
        "likes_count": likes_count,
        "dislikes_count": dislikes_count,
        "media_total": media_total,
        "parsed_at": datetime.now(),
    }

    return row


#  скролл и сбор отзывов одного автора 

def locate_profile_scroller(driver):
    """
    Ищем ближайший скроллируемый контейнер над блоком ugc-profile-reviews.
    """
    root = driver.find_element(By.CSS_SELECTOR, "div[data-chunk='ugc-profile-reviews']")
    el = root
    while el:
        if driver.execute_script("return arguments[0].scrollHeight > arguments[0].clientHeight;", el):
            return el
        el = driver.execute_script("return arguments[0].parentElement;", el)
    return driver.find_element(By.TAG_NAME, "body")


def collect_author_reviews(driver, author_row):
    profile_url = author_row["author_profile_url"]
    log(f"Открываю профиль автора: {author_row.get('author_name')} ({profile_url})")

    try:
        driver.get(profile_url)
    except TimeoutException:
        log(" Профиль грузился долго, продолжаем как есть")

    wait_if_captcha(driver)
    # ждём, пока вкладка "Отзывы" активируется
    try:
        WebDriverWait(driver, 60).until(
            EC.presence_of_element_located(
                (By.CSS_SELECTOR, "div[data-chunk='ugc-profile-reviews']")
            )
        )
    except TimeoutException:
        print(" Не дождались блока отзывов, пропускаю автора")
        return [], {}

    #  статистика профиля (подписчики / подписки / просмотры) 
    stats_vals = driver.find_elements(By.CSS_SELECTOR, "div.public-profile-stats-view__value")
    followers = following = profile_views = None
    if len(stats_vals) >= 3:
        try:
            followers = int(stats_vals[0].text.replace(" ", "").replace("к", "000").replace("м", "000000"))
        except ValueError:
            followers = None
        try:
            following = int(stats_vals[1].text.replace(" ", ""))
        except ValueError:
            following = None
        profile_views = stats_vals[2].text  # '9,2м' — оставим строкой

    #  счётчик "Отзывов N" 
    total_reviews_on_tab = None
    counter_text = safe_find(driver, "div.tabs-select-view__counter", "textContent", "")
    if counter_text and counter_text.isdigit():
        total_reviews_on_tab = int(counter_text)

    #  скролл отзывов 
    root = driver.find_element(By.CSS_SELECTOR, "div[data-chunk='ugc-profile-reviews']")
    scroller = locate_profile_scroller(driver)

    all_cards = []
    no_new_rounds = 0

    for round_idx in range(MAX_ROUNDS_SCROLL):
        try:
            cards_now = root.find_elements(By.CSS_SELECTOR, "div.public-profile-component__content-item")
        except StaleElementReferenceException:
            root = driver.find_element(By.CSS_SELECTOR, "div[data-chunk='ugc-profile-reviews']")
            cards_now = root.find_elements(By.CSS_SELECTOR, "div.public-profile-component__content-item")

        prev = len(all_cards)
        all_cards = cards_now

        print(f"[{round_idx+1}/{MAX_ROUNDS_SCROLL}] карточек видно: {len(all_cards)} "
              f"(ожидаем ≈ {total_reviews_on_tab})")

        if total_reviews_on_tab and len(all_cards) >= total_reviews_on_tab:
            print("Достигли количества, указанного на вкладке — стоп скролл.")
            break

        if len(all_cards) == prev:
            no_new_rounds += 1
        else:
            no_new_rounds = 0

        if no_new_rounds >= 7:
            print("Несколько проходов без новых карточек — останавливаюсь.")
            break

        if all_cards:
            last = all_cards[-1]
            try:
                driver.execute_script("arguments[0].scrollIntoView({block:'end'});", last)
                # чуть-чуть ещё вниз
                driver.execute_script("arguments[0].scrollTop += arguments[0].clientHeight * 0.3;", scroller)
            except StaleElementReferenceException:
                pass

        time.sleep(random.uniform(1.0, 2.0))

    print(f"Итого карточек для разбора: {len(all_cards)}")

    #  парсим карточки, фильтруем по годам 2023–2025 
    parsed_rows = []
    for i, card in enumerate(all_cards, start=1):
        row = parse_profile_review(card, author_row, i)
        y = row["review_year"]
        if y is None:
            continue
        if TARGET_YEAR_MIN <= y <= TARGET_YEAR_MAX:
            parsed_rows.append(row)

    profile_info = {
        "author_id": author_row["author_id"],
        "author_name": author_row.get("author_name"),
        "author_profile_url": profile_url,
        "followers": followers,
        "following": following,
        "profile_views": profile_views,
        "reviews_total_on_tab": total_reviews_on_tab,
        "reviews_parsed_total": len(all_cards),
        "reviews_parsed_2023_2025": len(parsed_rows),
        "parsed_at": datetime.now(),
    }

    print(f"  Отфильтровано отзывов 2023–2025: {len(parsed_rows)}")
    return parsed_rows, profile_info

def wait_if_captcha(driver, max_wait_minutes=15):
    start = time.time()
    warned = False

    while "captcha" in driver.current_url.lower():
        if not warned:
            log(" Обнаружена капча. Открой окно браузера и реши её вручную.")
            warned = True

        time.sleep(5)

        elapsed_min = (time.time() - start) / 60
        if elapsed_min > max_wait_minutes:
            log(f"Капча не исчезла за {max_wait_minutes} минут – продолжаю дальше (возможно, стоит перезапустить скрипт).")
            break

                
def append_df_csv(path, df):
    """Аккуратно дописывает df в CSV (без перетирания файла)."""
    if df.empty:
        return
    file_exists = os.path.exists(path)
    df.to_csv(
        path,
        mode="a" if file_exists else "w",   # если файла нет — создаём, если есть — дописываем
        header=not file_exists,             # заголовок только один раз
        index=False,
        encoding="utf-8-sig",
    )

def log(msg: str):
    """Печатаем сообщение и пишем его в лог-файл."""
    stamp = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
    line = f"[{stamp}] {msg}"
    print(line)
    try:
        with open(LOG_PATH, "a", encoding="utf-8") as f:
            f.write(line + "\n")
    except Exception:
        # Чтобы из-за проблем с логом не падал сам парсер
        pass

#  main 

def main():
    log("=== Старт парсинга профилей авторов ===")

    authors_df = pd.read_csv(AUTHORS_TO_PARSE_CSV)
    authors_df["author_id"] = authors_df["author_id"].astype(str)

    processed_ids = set()
    if os.path.exists(AUTHORS_PROFILES_CSV):
        try:
            existing = pd.read_csv(AUTHORS_PROFILES_CSV, usecols=["author_id"])
            processed_ids = set(existing["author_id"].astype(str))
            log(f"Уже обработано авторов: {len(processed_ids)}, пропускаю их.")
        except Exception as e:
            log(f"⚠ Не удалось прочитать {AUTHORS_PROFILES_CSV}: {e}")


    if processed_ids:
        authors_df = authors_df[~authors_df["author_id"].isin(processed_ids)].reset_index(drop=True)

    total_authors = len(authors_df)
    log(f"Осталось обработать авторов: {total_authors}")

    if total_authors == 0:
        log("Все авторы уже были обработаны ранее ")
        return

    driver = configure_browser()
    try:
        total_authors = len(authors_df)
        for idx, row in authors_df.iterrows():
            author_row = row.to_dict()
            log(f"=== Автор {idx+1}/{total_authors} — {author_row.get('author_name')} ({author_row.get('author_id')}) ===")

            try:
                reviews, profile_info = collect_author_reviews(driver, author_row)
            except Exception as e:
                log(f" Ошибка при обработке автора {author_row.get('author_id')}: {e}")
                continue

            prof_df = pd.DataFrame([profile_info]) if profile_info else pd.DataFrame()
            rev_df = pd.DataFrame(reviews)

            if not prof_df.empty:
                append_df_csv(AUTHORS_PROFILES_CSV, prof_df)

            if not rev_df.empty:
                append_df_csv(AUTHORS_REVIEWS_CSV, rev_df)

            log(f" Сохранено: профиль автора + {len(reviews)} отзывов")
    finally:
        driver.quit()
        log("=== Браузер закрыт ===")

    log("=== Парсинг профилей завершён ===")



if __name__ == "__main__":
    main()


[2025-11-26 23:20:57] === Старт парсинга профилей авторов ===
[2025-11-26 23:20:58] Уже обработано авторов: 552, пропускаю их.
[2025-11-26 23:20:58] Осталось обработать авторов: 5999
[2025-11-26 23:21:00] === Автор 1/5999 — Анна Данильченко (qwx15ev00x3hwtamfng6xjqvcm) ===
[2025-11-26 23:21:00] Открываю профиль автора: Анна Данильченко (https://yandex.com/maps/user/qwx15ev00x3hwtamfng6xjqvcm)
[1/300] карточек видно: 1 (ожидаем ≈ 1)
Достигли количества, указанного на вкладке — стоп скролл.
Итого карточек для разбора: 1
  ▶ медиа: total=0, preview=0, carousel_items=0
  Отфильтровано отзывов 2023–2025: 0
[2025-11-26 23:21:04] ✅ Сохранено: профиль автора + 0 отзывов
[2025-11-26 23:21:04] === Автор 2/5999 — Ирина Е. (czjkpazr0bv5xdphp8pugkxgfc) ===
[2025-11-26 23:21:04] Открываю профиль автора: Ирина Е. (https://yandex.com/maps/user/czjkpazr0bv5xdphp8pugkxgfc)
[1/300] карточек видно: 4 (ожидаем ≈ 4)
Достигли количества, указанного на вкладке — стоп скролл.
Итого карточек для разбора: 4
  ▶ 